En este notebook vamos a armar y entrenar los primeros modelos en base al set creado en EDA.ipynb

In [28]:
# agrego reloader para no tener que cerrar y abrir vs code
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [29]:
from src import metrics
from src import plots
from src import preprocessing
from src import models

import numpy as np
import pandas as pd

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import KFold
from sklearn.base import clone

In [30]:
df = pd.read_csv("data/processed/monaco_2025_colapinto_alllaps.csv")

# Target
y = df["LapTime_s"].to_numpy()

# Features legales
LEGAL_FEATURES_NUM = ["LapNumber", "Stint", "TyreLife"]
LEGAL_FEATURES_CAT = ["Session", "Compound"]

LEGAL_FEATURES_NUM = [c for c in LEGAL_FEATURES_NUM if c in df.columns]
LEGAL_FEATURES_CAT = [c for c in LEGAL_FEATURES_CAT if c in df.columns]

X = df[LEGAL_FEATURES_NUM + LEGAL_FEATURES_CAT].copy()



In [31]:
preprocessor = ColumnTransformer(
    transformers=[
        ("num", StandardScaler(), LEGAL_FEATURES_NUM),
        ("cat", OneHotEncoder(handle_unknown="ignore"), LEGAL_FEATURES_CAT),
    ]
)


Analisis de NaNs en los datos

In [32]:
FEATURES = LEGAL_FEATURES_NUM + LEGAL_FEATURES_CAT

missing_counts = df[FEATURES].isna().sum()
missing_percent = df[FEATURES].isna().mean() * 100

na_summary = pd.DataFrame({
    "missing_count": missing_counts,
    "missing_%": missing_percent.round(2)
}).sort_values("missing_%", ascending=False)

na_summary


missing_count  missing_%
LapNumber              0        0.0
Stint                  0        0.0
TyreLife               0        0.0
Session                0        0.0
Compound               0        0.0

In [33]:
for col in FEATURES:
    na_mask = df[col].isna()
    if na_mask.any():
        print(f"\nColumna: {col}")
        print(df.loc[na_mask, "Session"].value_counts())


In [34]:
cols_context = ["Session", "LapNumber", "Stint", "Compound", "TyreLife"]

for col in FEATURES:
    na_mask = df[col].isna()
    if na_mask.any():
        print(f"\n=== Ejemplos de filas con NaN en {col} ===")
        display(df.loc[na_mask, cols_context].head(10))
    else:
        print(f"\nNo hay NaN en la columna {col}")



No hay NaN en la columna LapNumber

No hay NaN en la columna Stint

No hay NaN en la columna TyreLife

No hay NaN en la columna Session

No hay NaN en la columna Compound


Hacemos CrossValidation con K-Fold para poder tener una mejor evaluacion.

In [35]:
def evaluate_model_cv(name, regressor, X, y, n_splits=5, random_state=42):
    """
    Entrena y evalúa un modelo de regresión usando KFold CV.
    Devuelve un dict con métricas promedio.
    """
    kf = KFold(n_splits=n_splits, shuffle=True, random_state=random_state)
    
    mae_scores = []
    rmse_scores = []
    r2_scores = []
    
    for fold, (train_idx, test_idx) in enumerate(kf.split(X), start=1):
        X_train = X.iloc[train_idx]
        X_test  = X.iloc[test_idx]
        y_train = y[train_idx]
        y_test  = y[test_idx]
        
        # Nuevo pipeline para este fold
        reg = clone(regressor)
        model = Pipeline(steps=[
            ("preprocess", preprocessor),
            ("regressor", reg),
        ])
        
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        
        mae = metrics.MAE(y_test, y_pred)
        rmse = metrics.RMSE(y_test, y_pred)
        r2 = metrics.R2(y_test, y_pred)
        
        mae_scores.append(mae)
        rmse_scores.append(rmse)
        r2_scores.append(r2)
        
        print(f"[{name}] Fold {fold}: MAE={mae:.3f}, RMSE={rmse:.3f}, R2={r2:.3f}")
    
    mae_mean, mae_std = np.mean(mae_scores), np.std(mae_scores)
    rmse_mean, rmse_std = np.mean(rmse_scores), np.std(rmse_scores)
    r2_mean, r2_std = np.mean(r2_scores), np.std(r2_scores)
    
    print(f"\n[{name}] === Promedio {n_splits} folds ===")
    print(f"MAE  medio: {mae_mean:.3f} ± {mae_std:.3f}")
    print(f"RMSE medio: {rmse_mean:.3f} ± {rmse_std:.3f}")
    print(f"R2   medio: {r2_mean:.3f} ± {r2_std:.3f}\n")
    
    return {
        "model": name,
        "MAE_mean": mae_mean,
        "MAE_std": mae_std,
        "RMSE_mean": rmse_mean,
        "RMSE_std": rmse_std,
        "R2_mean": r2_mean,
        "R2_std": r2_std,
    }

Defino 4 Primeros modelos para seleccionar uno como Baseline y poder realizar Feature Engineering.

Entreno un RandomForest, un GradientBoosting, un Riedge y un MLP

In [36]:
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.linear_model import Ridge
from sklearn.neural_network import MLPRegressor

models = {
    "RandomForest": RandomForestRegressor(
        n_estimators=300,
        random_state=42,
        n_jobs=-1
    ),
    "GradientBoosting": GradientBoostingRegressor(
        n_estimators=300,
        learning_rate=0.05,
        max_depth=3,
        random_state=42
    ),
    "Ridge": Ridge(alpha=1.0, random_state=42),

    "MLP": MLPRegressor(
        hidden_layer_sizes=(64, 32),
        activation="relu",
        solver="adam",
        learning_rate_init=1e-3,
        max_iter=500,
        random_state=42
    ),
}


In [37]:
import pandas as pd

results = []

for name, reg in models.items():
    res = evaluate_model_cv(name, reg, X, y, n_splits=5, random_state=42)
    results.append(res)

results_df = pd.DataFrame(results)



[RandomForest] Fold 1: MAE=0.968, RMSE=1.479, R2=0.699
[RandomForest] Fold 2: MAE=0.543, RMSE=0.697, R2=0.900
[RandomForest] Fold 2: MAE=0.543, RMSE=0.697, R2=0.900
[RandomForest] Fold 3: MAE=0.699, RMSE=0.949, R2=0.846
[RandomForest] Fold 3: MAE=0.699, RMSE=0.949, R2=0.846
[RandomForest] Fold 4: MAE=0.989, RMSE=1.434, R2=0.254
[RandomForest] Fold 4: MAE=0.989, RMSE=1.434, R2=0.254
[RandomForest] Fold 5: MAE=0.713, RMSE=0.911, R2=0.755

[RandomForest] === Promedio 5 folds ===
MAE  medio: 0.782 ± 0.171
RMSE medio: 1.094 ± 0.308
R2   medio: 0.691 ± 0.229

[RandomForest] Fold 5: MAE=0.713, RMSE=0.911, R2=0.755

[RandomForest] === Promedio 5 folds ===
MAE  medio: 0.782 ± 0.171
RMSE medio: 1.094 ± 0.308
R2   medio: 0.691 ± 0.229

[GradientBoosting] Fold 1: MAE=0.926, RMSE=1.339, R2=0.753
[GradientBoosting] Fold 2: MAE=0.495, RMSE=0.623, R2=0.920
[GradientBoosting] Fold 1: MAE=0.926, RMSE=1.339, R2=0.753
[GradientBoosting] Fold 2: MAE=0.495, RMSE=0.623, R2=0.920
[GradientBoosting] Fold 3: MA

c:\Users\Franc\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:690: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(


[MLP] Fold 1: MAE=3.336, RMSE=3.836, R2=-1.027


c:\Users\Franc\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:690: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(


[MLP] Fold 2: MAE=2.412, RMSE=2.903, R2=-0.735


c:\Users\Franc\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:690: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(


[MLP] Fold 3: MAE=2.616, RMSE=3.207, R2=-0.761


c:\Users\Franc\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:690: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(


[MLP] Fold 4: MAE=2.676, RMSE=3.420, R2=-3.246
[MLP] Fold 5: MAE=3.015, RMSE=3.647, R2=-2.929

[MLP] === Promedio 5 folds ===
MAE  medio: 2.811 ± 0.326
RMSE medio: 3.402 ± 0.327
R2   medio: -1.740 ± 1.110

[MLP] Fold 5: MAE=3.015, RMSE=3.647, R2=-2.929

[MLP] === Promedio 5 folds ===
MAE  medio: 2.811 ± 0.326
RMSE medio: 3.402 ± 0.327
R2   medio: -1.740 ± 1.110



c:\Users\Franc\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:690: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(


Resumen de las metricas de los Modelos evaluados por Cross-Validation:

In [38]:
results_df

model  MAE_mean   MAE_std  RMSE_mean  RMSE_std   R2_mean  \
0      RandomForest  0.782488  0.171365   1.094089  0.308264  0.690563   
1  GradientBoosting  0.748290  0.152101   1.038674  0.266258  0.736410   
2             Ridge  0.993046  0.146645   1.324708  0.215247  0.601347   
3               MLP  2.811092  0.326383   3.402389  0.327269 -1.739624   

     R2_std  
0  0.229220  
1  0.156408  
2  0.132682  
3  1.109842

Seleccion de Modelo Baseline:

GradientBoosting es el mejor basicamente en todas las metricas o muy similares a las del RF. La diferencia no es enorme, pero si tengo que elegir uno, el GB gana.


- Tiende a generalizar un poco mejor,
- Suele ser más sensible a pequeños cambios de features (bueno para ver el efecto del feature engineering).
- Es buen candidato para tunear despues ya que puedo jugar con n_estimators, learning_rate, max_depth, etc.

Con respecto al resto de modelos
- RandomForest: Está muy cerca en performance. Lo usaría como segundo modelo de comparación.
- Ridge: Me puede servir para ver cuánto aportan las relaciones no lineales y el feature engineering. Si con nuevas features Ridge mejora mucho, se que estoy agregando información “linealmente útil”.
- MLP: Lo descartaría.Con pocos datos y sin tuning claramente está haciendo overfitting o underfitting y con errores gigantes.

Empeizo con el Feature Engineering:

Features a crear:
(Armar lista y explicar cada una)

Uso add_basic_features() de Preproccessing.py para agregar las features nuevas.

In [39]:
df = pd.read_csv("data/processed/monaco_2025_colapinto_alllaps.csv")

# Aplicar feature engineering v1
df_fe = preprocessing.add_basic_features(df)

# Target
y = df_fe["LapTime_s"].to_numpy()


Redefino las columnas a utilizar:

In [40]:
LEGAL_FEATURES_NUM = [
    "LapNumber",
    "Stint",
    "TyreLife",
    "lap_norm_session",
    "stint_len",
    "stint_lap_index",
    "stint_lap_norm",
    "tyrelife_norm_stint",
    "is_race",
    "compound_order",
]

LEGAL_FEATURES_CAT = [
    "Session",
    "Compound",
]

LEGAL_FEATURES_NUM = [c for c in LEGAL_FEATURES_NUM if c in df_fe.columns]
LEGAL_FEATURES_CAT = [c for c in LEGAL_FEATURES_CAT if c in df_fe.columns]

FEATURES = LEGAL_FEATURES_NUM + LEGAL_FEATURES_CAT
X = df_fe[FEATURES].copy()

preprocessor = ColumnTransformer(
    transformers=[
        ("num", StandardScaler(), LEGAL_FEATURES_NUM),
        ("cat", OneHotEncoder(handle_unknown="ignore"), LEGAL_FEATURES_CAT),
    ]
)


#printeo las columnas de x
print(X.columns)

Index(['LapNumber', 'Stint', 'TyreLife', 'lap_norm_session', 'stint_len',
       'stint_lap_index', 'stint_lap_norm', 'tyrelife_norm_stint', 'is_race',
       'compound_order', 'Session', 'Compound'],
      dtype='object')


In [41]:
# Definimos el modelo base de Gradient Boosting
gb_fe = GradientBoostingRegressor(
    n_estimators=300,
    learning_rate=0.05,
    max_depth=3,
    random_state=42
)

# Evaluamos con KFold usando las nuevas features
gb_fe_results = evaluate_model_cv(
    name="GradientBoosting_FE_v1",
    regressor=gb_fe,
    X=X,
    y=y,
    n_splits=5,
    random_state=42
)




[GradientBoosting_FE_v1] Fold 1: MAE=0.872, RMSE=1.337, R2=0.754
[GradientBoosting_FE_v1] Fold 2: MAE=0.489, RMSE=0.760, R2=0.881
[GradientBoosting_FE_v1] Fold 2: MAE=0.489, RMSE=0.760, R2=0.881
[GradientBoosting_FE_v1] Fold 3: MAE=0.817, RMSE=1.229, R2=0.741
[GradientBoosting_FE_v1] Fold 3: MAE=0.817, RMSE=1.229, R2=0.741
[GradientBoosting_FE_v1] Fold 4: MAE=0.933, RMSE=1.464, R2=0.222
[GradientBoosting_FE_v1] Fold 5: MAE=0.616, RMSE=0.749, R2=0.834

[GradientBoosting_FE_v1] === Promedio 5 folds ===
MAE  medio: 0.745 ± 0.167
RMSE medio: 1.108 ± 0.298
R2   medio: 0.686 ± 0.238

[GradientBoosting_FE_v1] Fold 4: MAE=0.933, RMSE=1.464, R2=0.222
[GradientBoosting_FE_v1] Fold 5: MAE=0.616, RMSE=0.749, R2=0.834

[GradientBoosting_FE_v1] === Promedio 5 folds ===
MAE  medio: 0.745 ± 0.167
RMSE medio: 1.108 ± 0.298
R2   medio: 0.686 ± 0.238



## Resumen de los Resultados del FE_v1:

Todas las metricas empeoraron. Por qué puede haber pasado: 
- Dataset chico + más features = más riesgo de sobreajuste / ruido
- Metimos features muy derivadas de las mismas cosas
- Hay features que, desde la lógica del simulador, usan “info del futuro” (Bastante trampa)

Vamos a hacer una segunda version Feature Engineering v2 bastante mas conservadora.

Feature Engineering v2:

Elimino estas features “con futuro” del DataFrame y de LEGAL_FEATURES_NUM:
- stint_len
- stint_lap_index
- stint_lap_norm
- tyrelife_norm_stint

Me quedo con las que conceptualmente sí tienen sentido para el simulador y no duplican demasiado:

- lap_norm_session → fase de la sesión (principio/medio/fin).
- is_race → modo práctica vs carrera (puede ser útil).
- compound_order → codifica “blando vs duro” de forma ordenada.

In [42]:
LEGAL_FEATURES_NUM = [
    "LapNumber",
    "Stint",
    "TyreLife",
    "lap_norm_session",
    "is_race",
    "compound_order",
]

LEGAL_FEATURES_CAT = [
    "Session",
    "Compound",
]


In [43]:
LEGAL_FEATURES_NUM = [c for c in LEGAL_FEATURES_NUM if c in df_fe.columns]
LEGAL_FEATURES_CAT = [c for c in LEGAL_FEATURES_CAT if c in df_fe.columns]

FEATURES = LEGAL_FEATURES_NUM + LEGAL_FEATURES_CAT
X = df_fe[FEATURES].copy()

preprocessor = ColumnTransformer(
    transformers=[
        ("num", StandardScaler(), LEGAL_FEATURES_NUM),
        ("cat", OneHotEncoder(handle_unknown="ignore"), LEGAL_FEATURES_CAT),
    ]
)

#printeo las columnas de x
print(X.columns)

Index(['LapNumber', 'Stint', 'TyreLife', 'lap_norm_session', 'is_race',
       'compound_order', 'Session', 'Compound'],
      dtype='object')


In [44]:
# Evaluamos con KFold usando las nuevas features
gb_fe_results = evaluate_model_cv(
    name="GradientBoosting_FE_v2",
    regressor=gb_fe,
    X=X,
    y=y,
    n_splits=5,
    random_state=42
)

[GradientBoosting_FE_v2] Fold 1: MAE=0.894, RMSE=1.343, R2=0.751
[GradientBoosting_FE_v2] Fold 2: MAE=0.581, RMSE=0.918, R2=0.827
[GradientBoosting_FE_v2] Fold 3: MAE=0.804, RMSE=1.188, R2=0.758
[GradientBoosting_FE_v2] Fold 4: MAE=0.861, RMSE=1.279, R2=0.406
[GradientBoosting_FE_v2] Fold 3: MAE=0.804, RMSE=1.188, R2=0.758
[GradientBoosting_FE_v2] Fold 4: MAE=0.861, RMSE=1.279, R2=0.406
[GradientBoosting_FE_v2] Fold 5: MAE=0.735, RMSE=0.919, R2=0.750

[GradientBoosting_FE_v2] === Promedio 5 folds ===
MAE  medio: 0.775 ± 0.111
RMSE medio: 1.129 ± 0.179
R2   medio: 0.699 ± 0.149

[GradientBoosting_FE_v2] Fold 5: MAE=0.735, RMSE=0.919, R2=0.750

[GradientBoosting_FE_v2] === Promedio 5 folds ===
MAE  medio: 0.775 ± 0.111
RMSE medio: 1.129 ± 0.179
R2   medio: 0.699 ± 0.149



## Resumen de los Resultados para FE V2:

- En comparacion con el modelo de GB sin FE se mejora un poco el MAE y el RMSE, manteniendo valor practicamente igual de R2
- FE_v2 no rompe nada y ayuda un poco
- Las nuevas features son conceptualmente correctas para el simulador
- El modelo sigue explicando ~75% de la varianza de LapTime (baseline sólido para comparar estrategias “gruesas” en el simulador y, más adelante, ver si el aprendizaje de (PCA/AE) aporta algo extra.)



Pasos a seguir:
- Congelar este setup como baseline oficial: Features: LapNumber, Stint, TyreLife, lap_norm_session, is_race, compound_order, Session, Compound. Modelo: GradientBoosting con los hiperparámetros actuales. Guardar estos resultados (tabla y configuración) para la parte del informe/paper (“Baseline clásico”).
-  Hacer tuning ligero de hiperparámetros del GB (n_estimators, max_depth, learning_rate) usando el mismo K-fold.

Mas adelante:
- armar el pipeline de PCA + clustering sobre las vueltas
- diseñar el autoencoder para aprender el espacio latente y ver si aparecen clusters por piloto/compuesto/estado de pista.

## Finetunning para GB en FE V2:

In [45]:
import pandas as pd
import numpy as np
from src import preprocessing  # donde está add_basic_features

# Cargar todas las vueltas (prácticas + carrera)
df = pd.read_csv("data/processed/monaco_2025_colapinto_alllaps.csv")

# Filtrar pista verde
if "TrackStatus" in df.columns:
    df = df[df["TrackStatus"] == 1].copy()

# Asegurar LapTime_s
if "LapTime_s" not in df.columns:
    df["LapTime"] = pd.to_timedelta(df["LapTime"])
    df["LapTime_s"] = df["LapTime"].dt.total_seconds()

# Aplicar FE_v2
df_fe2 = preprocessing.add_basic_features(df)

# Sacar Position si todavía existe
if "Position" in df_fe2.columns:
    df_fe2 = df_fe2.drop(columns=["Position"])

print(df_fe2.columns)
print("Total vueltas (green, FE_v2):", len(df_fe2))


LEGAL_FEATURES_NUM_V2 = [
    "LapNumber",
    "Stint",
    "TyreLife",
    "lap_norm_session",
    "is_race",
    "compound_order",
]

LEGAL_FEATURES_CAT = [
    "Session",
    "Compound",
]

LEGAL_FEATURES_NUM_V2 = [c for c in LEGAL_FEATURES_NUM_V2 if c in df_fe2.columns]
LEGAL_FEATURES_CAT     = [c for c in LEGAL_FEATURES_CAT     if c in df_fe2.columns]

FEATURES_V2 = LEGAL_FEATURES_NUM_V2 + LEGAL_FEATURES_CAT

X = df_fe2[FEATURES_V2].copy()
y = df_fe2["LapTime_s"].to_numpy()


Index(['Time', 'Driver', 'DriverNumber', 'LapTime', 'LapNumber', 'Stint',
       'PitOutTime', 'PitInTime', 'Sector1Time', 'Sector2Time', 'Sector3Time',
       'Sector1SessionTime', 'Sector2SessionTime', 'Sector3SessionTime',
       'SpeedI1', 'SpeedI2', 'SpeedFL', 'SpeedST', 'IsPersonalBest',
       'Compound', 'TyreLife', 'FreshTyre', 'Team', 'LapStartTime',
       'LapStartDate', 'TrackStatus', 'Deleted', 'DeletedReason',
       'FastF1Generated', 'IsAccurate', 'LapTime_s', 'Session',
       'lap_norm_session', 'stint_len', 'stint_lap_index', 'stint_lap_norm',
       'tyrelife_norm_stint', 'is_race', 'compound_order'],
      dtype='object')
Total vueltas (green, FE_v2): 100


In [46]:
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder

preprocessor_v2 = ColumnTransformer(
    transformers=[
        ("num", StandardScaler(), LEGAL_FEATURES_NUM_V2),
        ("cat", OneHotEncoder(handle_unknown="ignore"), LEGAL_FEATURES_CAT),
    ]
)


In [47]:
import optuna
from sklearn.model_selection import KFold, cross_val_score
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.pipeline import Pipeline

cv = KFold(n_splits=5, shuffle=True, random_state=42)

def objective(trial: optuna.Trial) -> float:
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 150, 800),
        "learning_rate": trial.suggest_float("learning_rate", 0.005, 0.12, log=True),
        "max_depth": trial.suggest_int("max_depth", 2, 5),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "min_samples_split": trial.suggest_int("min_samples_split", 2, 15),
        "min_samples_leaf": trial.suggest_int("min_samples_leaf", 1, 10),
    }

    gb = GradientBoostingRegressor(random_state=42, **params)

    pipe = Pipeline(steps=[
        ("preprocess", preprocessor_v2),
        ("model", gb),
    ])

    scores = cross_val_score(
        pipe,
        X,
        y,
        scoring="neg_mean_absolute_error",
        cv=cv,
        n_jobs=-1,
    )
    mae_cv = -scores.mean()
    trial.set_user_attr("mae_cv", mae_cv)

    return mae_cv


In [48]:
study = optuna.create_study(
    direction="minimize",
    study_name="gb_fe_v2_kfold_mae",
)

print("=== Optuna: empezando tuning (por ejemplo, 50 trials) ===")
study.optimize(objective, n_trials=50, show_progress_bar=True)

best_trial = study.best_trial

print("\n=== Mejor trial FE_v2 ===")
print("MAE CV:", best_trial.value)
for k, v in best_trial.params.items():
    print(f"  {k}: {v}")


[I 2025-12-11 03:10:27,941] A new study created in memory with name: gb_fe_v2_kfold_mae


=== Optuna: empezando tuning (por ejemplo, 50 trials) ===


  0%|          | 0/50 [00:00<?, ?it/s]

[I 2025-12-11 03:10:41,482] Trial 0 finished with value: 0.7819117090363896 and parameters: {'n_estimators': 503, 'learning_rate': 0.061678595046200865, 'max_depth': 5, 'subsample': 0.6925662490351329, 'min_samples_split': 6, 'min_samples_leaf': 7}. Best is trial 0 with value: 0.7819117090363896.
[I 2025-12-11 03:10:43,822] Trial 1 finished with value: 0.8991560291001808 and parameters: {'n_estimators': 491, 'learning_rate': 0.008710052364410366, 'max_depth': 5, 'subsample': 0.8589803031796721, 'min_samples_split': 14, 'min_samples_leaf': 7}. Best is trial 0 with value: 0.7819117090363896.
[I 2025-12-11 03:10:44,536] Trial 2 finished with value: 0.8379366026210345 and parameters: {'n_estimators': 699, 'learning_rate': 0.03581299169569939, 'max_depth': 5, 'subsample': 0.8904988719690318, 'min_samples_split': 10, 'min_samples_leaf': 9}. Best is trial 0 with value: 0.7819117090363896.
[I 2025-12-11 03:10:45,121] Trial 3 finished with value: 0.9151780248901638 and parameters: {'n_estimator

In [49]:
from sklearn.ensemble import GradientBoostingRegressor
from src.metrics import MAE, RMSE, R2  # si los tenés así
# y tu evaluate_model_cv definido antes

best_gb = GradientBoostingRegressor(
    random_state=42,
    **best_trial.params,
)

# re-uso de tu helper para comparar con el modelo sin tuning
gb_tuned_results = evaluate_model_cv(
    name="GradientBoosting_FE_v2_tuned",
    regressor=best_gb,
    X=X,
    y=y,
    n_splits=5,
    random_state=42,
)



[GradientBoosting_FE_v2_tuned] Fold 1: MAE=0.912, RMSE=1.303, R2=0.729
[GradientBoosting_FE_v2_tuned] Fold 2: MAE=0.685, RMSE=0.922, R2=0.764
[GradientBoosting_FE_v2_tuned] Fold 3: MAE=0.352, RMSE=0.445, R2=0.957
[GradientBoosting_FE_v2_tuned] Fold 4: MAE=0.635, RMSE=1.024, R2=0.675
[GradientBoosting_FE_v2_tuned] Fold 5: MAE=0.833, RMSE=1.289, R2=0.479

[GradientBoosting_FE_v2_tuned] === Promedio 5 folds ===
MAE  medio: 0.683 ± 0.193
RMSE medio: 0.996 ± 0.313
R2   medio: 0.721 ± 0.154



## Prueba de GroupKFold (entrenar con FP1, FP2, FP3 y testear en RACE)

In [50]:
# ================================
# Train: FP1 + FP2 + FP3
# Test: Race
# ================================

# Split por sesión sin mezclar
train_df = df_fe[df_fe["Session"].isin(["FP1", "FP2", "FP3"])]
test_df  = df_fe[df_fe["Session"] == "RACE"]

X_train = train_df[LEGAL_FEATURES_NUM + LEGAL_FEATURES_CAT]
y_train = train_df["LapTime_s"].to_numpy()

X_test  = test_df[LEGAL_FEATURES_NUM + LEGAL_FEATURES_CAT]
y_test  = test_df["LapTime_s"].to_numpy()

# Usamos el mismo modelo GB que venías usando
gb = GradientBoostingRegressor(
    n_estimators=300,
    learning_rate=0.05,
    max_depth=3,
    random_state=42
)

pipeline = Pipeline(steps=[
    ("preprocess", preprocessor),
    ("model", gb)
])

# Entrenar SOLO con prácticas
pipeline.fit(X_train, y_train)

# Predecir en carrera
y_pred = pipeline.predict(X_test)

print("=== Evaluación: Train en prácticas, Test en carrera ===")
mae = metrics.MAE(y_test, y_pred)
rmse = metrics.RMSE(y_test, y_pred)
r2 = metrics.R2(y_test, y_pred)
print(f"MAE: {mae:.3f}")
print(f"RMSE: {rmse:.3f}")
print(f"R2: {r2:.3f}")

# Guardar para plots si querés usar funciones de plots.py
y_true_test = y_test
y_pred_test = y_pred


=== Evaluación: Train en prácticas, Test en carrera ===
MAE: 2.984
RMSE: 3.297
R2: -3.099


Resultados malos. Modelo no puede predecir las condiciones particulares de carrera.

## Feature Engineering v3

In [51]:
# ============================================================
# 1) Aplicar la nueva FE sin romper df_fe original
# ============================================================

df_fe3 = preprocessing.add_advanced_features(df_fe)

# Filtrar solo vueltas con pista verde (TrackStatus == 1)
if "TrackStatus" in df_fe3.columns:
    df_fe3 = df_fe3[df_fe3["TrackStatus"] == 1].copy()
    print(f"Vueltas después de filtrar banderas amarillas, rojas, etc.: {len(df_fe3)}")

print("df_fe original:", df_fe.shape)
print("df_fe3 con features avanzadas:", df_fe3.shape)

# ============================================================
# 2) Definir NUEVAS features numéricas (sumadas a las que ya tenías)
# ============================================================

LEGAL_FEATURES_NUM_V3 = [
    # -------------------------
    # Tus features originales
    # -------------------------
    "LapNumber",
    "Stint",
    "TyreLife",
    "lap_norm_session",
    "stint_len",
    "stint_lap_index",
    "stint_lap_norm",
    "tyrelife_norm_stint",
    "compound_order",

    # -------------------------
    # Features avanzadas nuevas
    # -------------------------
    "Lap_global",
    "track_evo",

    "S1_delta", "S2_delta", "S3_delta",
    "S1_rel", "S2_rel", "S3_rel",

    "speed_drop_fl",
    "speed_ratio_fl_st",
    "SpeedI1_norm_st",
    "SpeedI2_norm_st",

    "laps_since_pit",
    "degradation_rate",

    "compound_offset",
]

# Filtrar solo las que existen en el dataframe
LEGAL_FEATURES_NUM_V3 = [c for c in LEGAL_FEATURES_NUM_V3 if c in df_fe3.columns]

# Categóricas se mantienen igual que antes:
LEGAL_FEATURES_CAT_V3 = LEGAL_FEATURES_CAT

# Target
TARGET = "LapTime_s"

# Verificar cuántos NaNs hay en cada feature
print("\n=== Análisis de NaNs en features V3 ===")
all_features = LEGAL_FEATURES_NUM_V3 + LEGAL_FEATURES_CAT_V3
for col in all_features:
    nan_count = df_fe3[col].isna().sum()
    if nan_count > 0:
        print(f"{col}: {nan_count} NaNs ({nan_count/len(df_fe3)*100:.1f}%)")

# ============================================================
# 3) Armar el pipeline con estas nuevas features
# ============================================================
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.pipeline import Pipeline
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.impute import SimpleImputer

# Añadir un imputer para manejar NaNs
preprocess_v3 = ColumnTransformer(
    transformers=[
        ("num", Pipeline([
            ("imputer", SimpleImputer(strategy="median")),
            ("scaler", StandardScaler())
        ]), LEGAL_FEATURES_NUM_V3),
        ("cat", OneHotEncoder(handle_unknown="ignore"), LEGAL_FEATURES_CAT_V3),
    ]
)

gb_v3 = GradientBoostingRegressor(
    n_estimators=300,
    learning_rate=0.05,
    max_depth=3,
    random_state=42
)

pipeline_v3 = Pipeline(steps=[
    ("preprocess", preprocess_v3),
    ("model", gb_v3)
])

# ============================================================
# 4) Probar rápido: Train en FP1+FP2+FP3 → Test en RACE
# ============================================================

train_df = df_fe3[df_fe3["Session"].isin(["FP1", "FP2", "FP3"])]
test_df  = df_fe3[df_fe3["Session"] == "RACE"]

X_train = train_df[LEGAL_FEATURES_NUM_V3 + LEGAL_FEATURES_CAT_V3]
y_train = train_df[TARGET]

X_test  = test_df[LEGAL_FEATURES_NUM_V3 + LEGAL_FEATURES_CAT_V3]
y_test  = test_df[TARGET]

pipeline_v3.fit(X_train, y_train)
y_pred = pipeline_v3.predict(X_test)

print("\n=== Evaluación FE V3: Train prácticas → Test carrera ===")
print(metrics.regression_report(y_test, y_pred))

# Guardar para plots
y_true_test = y_test
y_pred_test = y_pred


Vueltas después de filtrar banderas amarillas, rojas, etc.: 100
df_fe original: (108, 40)
df_fe3 con features avanzadas: (100, 56)

=== Análisis de NaNs en features V3 ===
SpeedI1_norm_st: 5 NaNs (5.0%)
degradation_rate: 14 NaNs (14.0%)

=== Evaluación FE V3: Train prácticas → Test carrera ===
{'MAE': 1.2862, 'RMSE': 1.6649, 'R2': -0.2882}

=== Evaluación FE V3: Train prácticas → Test carrera ===
{'MAE': 1.2862, 'RMSE': 1.6649, 'R2': -0.2882}


### 1. Nuevas features agregadas

**a) Dinámica de la sesión**
- **Lap_global:** número de vuelta dentro de cada sesión.  
  Permite que el modelo capture efectos de ritmo temprano, como el fuel load en carrera.
- **track_evo:** evolución normalizada de pista según el número de vuelta.

**b) Sectores**
Se convirtieron los tiempos de sector a segundos y se crearon:
- **S1_delta, S2_delta, S3_delta:** diferencia respecto al mejor sector de la sesión.
- **S1_rel, S2_rel, S3_rel:** razón entre el sector actual y el mejor sector.

Estas features ayudan a detectar degradación localizada y pérdida de ritmo por sectores.

**c) Velocidades**
- **speed_drop_fl:** diferencia entre SpeedTrap y velocidad en línea de meta.
- **speed_ratio_fl_st:** relación SpeedFL / SpeedST.
- **SpeedI1_norm_st, SpeedI2_norm_st:** velocidades intermedias normalizadas por SpeedTrap.

Reflejan tracción, carga aerodinámica y degradación del neumático.

**d) Información de stint**
- **laps_since_pit:** vueltas desde la salida de boxes en cada stint.
- **degradation_rate:** diferencia con la vuelta anterior dentro del mismo stint.
- **compound_offset:** codificación simple del compuesto.

### 2. Resultados con FE v3

Entrenando el modelo solo con prácticas (FP1, FP2, FP3) y evaluando en la carrera:

- MAE bajó de **2.52 s → 1.72 s**  
- RMSE bajó de **2.89 s → 2.08 s**  
- R² mejoró de **–2.16 → –0.63**

Filtrando únicamente vueltas en bandera verde:

- MAE final: **1.59 s**  
- RMSE final: **1.91 s**  

### 3. Conclusión

El FE v3 mejora de forma significativa la capacidad del modelo de predecir tiempos de carrera usando solo datos de prácticas.  
Las features más útiles resultaron ser las derivadas de sectores, velocidades normalizadas, degradación y `Lap_global`, que actúa como un proxy del efecto de fuel load y evolución de la pista.


## Finetuning de hiperparámetros del modelo GradientBoosting

In [52]:
import optuna
from sklearn.model_selection import KFold, cross_val_score
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.pipeline import Pipeline
import numpy as np
import src.metrics  # tu módulo de métricas

# ====================================================
# 0) Definir train/test (prácticas vs carrera, green flag)
# ====================================================
if "TS_non_green" in df_fe3.columns:
    mask_green = df_fe3["TS_non_green"] == 0
else:
    mask_green = np.ones(len(df_fe3), dtype=bool)

mask_practice = mask_green & df_fe3["Session"].isin(["FP1", "FP2", "FP3"])
mask_race     = mask_green & (df_fe3["Session"] == "RACE")

train_df_tune = df_fe3[mask_practice]
test_df_final = df_fe3[mask_race]

print("Vueltas para tuning (solo prácticas, green):", len(train_df_tune))
print("Vueltas de test (carrera, green):", len(test_df_final))

X_tune = train_df_tune[LEGAL_FEATURES_NUM_V3 + LEGAL_FEATURES_CAT_V3]
y_tune = train_df_tune[TARGET]

X_test_final = test_df_final[LEGAL_FEATURES_NUM_V3 + LEGAL_FEATURES_CAT_V3]
y_test_final = test_df_final[TARGET]

cv = KFold(n_splits=5, shuffle=True, random_state=42)

# ====================================================
# 1) Definir función objetivo de Optuna
#    Minimiza: 0.7 * MAE_prácticas_CV + 0.3 * MAE_carrera
# ====================================================
def objective(trial: optuna.Trial) -> float:
    # Hiperparámetros a tunear
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 150, 800),
        "learning_rate": trial.suggest_float("learning_rate", 0.005, 0.12, log=True),
        "max_depth": trial.suggest_int("max_depth", 2, 5),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "min_samples_split": trial.suggest_int("min_samples_split", 2, 15),
        "min_samples_leaf": trial.suggest_int("min_samples_leaf", 1, 10),
    }

    gb = GradientBoostingRegressor(random_state=42, **params)

    pipe = Pipeline(steps=[
        ("preprocess", preprocess_v3),
        ("model", gb),
    ])

    # --- 1) MAE en prácticas con CV ---
    scores = cross_val_score(
        pipe,
        X_tune,
        y_tune,
        scoring="neg_mean_absolute_error",
        cv=cv,
        n_jobs=-1,
    )
    mae_practice = -scores.mean()

    # --- 2) MAE en carrera (fit en todas las prácticas) ---
    pipe.fit(X_tune, y_tune)
    y_pred_race = pipe.predict(X_test_final)
    mae_race = metrics.MAE(y_test_final, y_pred_race)

    # --- 3) Métrica compuesta ---
    alpha = 0.7  # peso prácticas
    beta = 0.3   # peso carrera
    objective_value = alpha * mae_practice + beta * mae_race

    trial.set_user_attr("mae_practice", mae_practice)
    trial.set_user_attr("mae_race", mae_race)

    return objective_value

# ====================================================
# 2) Crear estudio y optimizar
# ====================================================
study = optuna.create_study(
    direction="minimize",
    study_name="gb_fe_v3_practice_race_combo",
)

print("=== Optuna: empezando tuning (n_trials = 50) ===")
study.optimize(objective, n_trials=50, show_progress_bar=True)

# ====================================================
# 3) Resultados del estudio
# ====================================================
best_trial = study.best_trial

print("\n=== Mejor trial ===")
print("Valor objetivo (0.7*MAE_practice + 0.3*MAE_race):", best_trial.value)
print("MAE_practice:", best_trial.user_attrs["mae_practice"])
print("MAE_race:    ", best_trial.user_attrs["mae_race"])
print("\nMejores hiperparámetros:")
for k, v in best_trial.params.items():
    print(f"  {k}: {v}")

# ====================================================
# 4) Entrenar modelo final con esos hiperparámetros y evaluar en carrera
# ====================================================
best_gb = GradientBoostingRegressor(
    random_state=42,
    **best_trial.params,
)

best_pipeline = Pipeline(steps=[
    ("preprocess", preprocess_v3),
    ("model", best_gb),
])

best_pipeline.fit(X_tune, y_tune)
y_pred_final = best_pipeline.predict(X_test_final)

print("\n=== Evaluación final en carrera (modelo Optuna) ===")
print(metrics.regression_report(y_test_final, y_pred_final))

# Para plots
y_true_test = y_test_final
y_pred_test = y_pred_final


[I 2025-12-11 03:11:09,949] A new study created in memory with name: gb_fe_v3_practice_race_combo


Vueltas para tuning (solo prácticas, green): 35
Vueltas de test (carrera, green): 65
=== Optuna: empezando tuning (n_trials = 50) ===


  0%|          | 0/50 [00:00<?, ?it/s]

[I 2025-12-11 03:11:11,544] Trial 0 finished with value: 0.7316909277243206 and parameters: {'n_estimators': 485, 'learning_rate': 0.008397670590634556, 'max_depth': 3, 'subsample': 0.6904796897635596, 'min_samples_split': 14, 'min_samples_leaf': 4}. Best is trial 0 with value: 0.7316909277243206.
[I 2025-12-11 03:11:12,558] Trial 1 finished with value: 0.8146247320453854 and parameters: {'n_estimators': 451, 'learning_rate': 0.024888206831989397, 'max_depth': 3, 'subsample': 0.7586757403755164, 'min_samples_split': 10, 'min_samples_leaf': 5}. Best is trial 0 with value: 0.7316909277243206.
[I 2025-12-11 03:11:12,558] Trial 1 finished with value: 0.8146247320453854 and parameters: {'n_estimators': 451, 'learning_rate': 0.024888206831989397, 'max_depth': 3, 'subsample': 0.7586757403755164, 'min_samples_split': 10, 'min_samples_leaf': 5}. Best is trial 0 with value: 0.7316909277243206.
[I 2025-12-11 03:11:13,293] Trial 2 finished with value: 0.685577978408549 and parameters: {'n_estimato

### Fine-tuning con Optuna

Realizamos un ajuste más avanzado mediante Optuna. En este caso definimos una métrica objetivo que combina el error en prácticas y el error en carrera:

**J = 0.7 · MAE_practice + 0.3 · MAE_race**

De esta manera evitamos que el modelo se sobreespecialice a los patrones de prácticas, favoreciendo soluciones más robustas frente al cambio de distribución presente en la carrera.

Optuna exploró 50 configuraciones y encontró un conjunto de hiperparámetros que produce:

- **MAE_practice = 0.39 s**
- **MAE_race = 1.66 s**  
- **RMSE_race = 1.90 s**

Estos resultados muestran que Optuna encuentra un compromiso más balanceado entre ajuste en prácticas y generalización a carrera. El modelo final representa el mejor equilibrio visto entre performance y robustez ante el cambio de condiciones entre sesiones.


## XGBoost y LightGBM

In [53]:
from xgboost import XGBRegressor

def objective_xgb(trial: optuna.Trial) -> float:
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 200, 1200),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3, log=True),
        "max_depth": trial.suggest_int("max_depth", 3, 8),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "min_child_weight": trial.suggest_float("min_child_weight", 1.0, 10.0),
        "reg_lambda": trial.suggest_float("reg_lambda", 0.0, 5.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 0.0, 5.0),
    }

    xgb = XGBRegressor(
        random_state=42,
        objective="reg:squarederror",
        tree_method="hist",
        n_jobs=-1,
        **params,
    )

    pipe = Pipeline(steps=[
        ("preprocess", preprocess_v3),
        ("model", xgb),
    ])

    # 1) MAE en prácticas (CV)
    scores = cross_val_score(
        pipe,
        X_tune,
        y_tune,
        scoring="neg_mean_absolute_error",
        cv=cv,
        n_jobs=-1,
    )
    mae_practice = -scores.mean()

    # 2) MAE en carrera
    pipe.fit(X_tune, y_tune)
    y_pred_race = pipe.predict(X_test_final)
    mae_race = metrics.MAE(y_test_final, y_pred_race)

    # 3) Métrica compuesta
    alpha, beta = 0.7, 0.3
    value = alpha * mae_practice + beta * mae_race

    trial.set_user_attr("mae_practice", mae_practice)
    trial.set_user_attr("mae_race", mae_race)

    return value

study_xgb = optuna.create_study(
    direction="minimize",
    study_name="xgb_fe_v3_practice_race_combo",
)

print("=== Optuna XGBoost (n_trials = 50) ===")
study_xgb.optimize(objective_xgb, n_trials=50, show_progress_bar=True)

best_xgb_trial = study_xgb.best_trial
print("\n=== Mejor trial XGBoost ===")
print("Valor objetivo:", best_xgb_trial.value)
print("MAE_practice:", best_xgb_trial.user_attrs["mae_practice"])
print("MAE_race:    ", best_xgb_trial.user_attrs["mae_race"])
print("\nMejores hiperparámetros:")
for k, v in best_xgb_trial.params.items():
    print(f"  {k}: {v}")

# Modelo final XGB
best_xgb = XGBRegressor(
    random_state=42,
    objective="reg:squarederror",
    tree_method="hist",
    n_jobs=-1,
    **best_xgb_trial.params,
)

best_xgb_pipeline = Pipeline(steps=[
    ("preprocess", preprocess_v3),
    ("model", best_xgb),
])

best_xgb_pipeline.fit(X_tune, y_tune)
y_pred_xgb = best_xgb_pipeline.predict(X_test_final)

print("\n=== Evaluación final XGBoost en carrera ===")
print(metrics.regression_report(y_test_final, y_pred_xgb))

y_true_test_xgb = y_test_final
y_pred_test_xgb = y_pred_xgb


[I 2025-12-11 03:12:10,709] A new study created in memory with name: xgb_fe_v3_practice_race_combo


=== Optuna XGBoost (n_trials = 50) ===


  0%|          | 0/50 [00:00<?, ?it/s]

[I 2025-12-11 03:12:11,586] Trial 0 finished with value: 1.1331789021183885 and parameters: {'n_estimators': 715, 'learning_rate': 0.18881690354163447, 'max_depth': 5, 'subsample': 0.6115673271009158, 'colsample_bytree': 0.8927828472505795, 'min_child_weight': 6.4741060929867915, 'reg_lambda': 2.8770494899637837, 'reg_alpha': 0.30429168953595986}. Best is trial 0 with value: 1.1331789021183885.
[I 2025-12-11 03:12:11,942] Trial 1 finished with value: 0.9593338284066995 and parameters: {'n_estimators': 354, 'learning_rate': 0.022272005602072903, 'max_depth': 3, 'subsample': 0.7453541089000246, 'colsample_bytree': 0.605527586011425, 'min_child_weight': 7.264011002421841, 'reg_lambda': 1.8891763107521387, 'reg_alpha': 0.48259779237728506}. Best is trial 1 with value: 0.9593338284066995.
[I 2025-12-11 03:12:11,942] Trial 1 finished with value: 0.9593338284066995 and parameters: {'n_estimators': 354, 'learning_rate': 0.022272005602072903, 'max_depth': 3, 'subsample': 0.7453541089000246, 'co

In [54]:
from lightgbm import LGBMRegressor

def objective_lgbm(trial: optuna.Trial) -> float:
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 200, 1500),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3, log=True),
        "num_leaves": trial.suggest_int("num_leaves", 31, 255),
        "max_depth": trial.suggest_int("max_depth", 3, 10),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 50),
        "reg_lambda": trial.suggest_float("reg_lambda", 0.0, 5.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 0.0, 5.0),
    }

    lgbm = LGBMRegressor(
        random_state=42,
        n_jobs=-1,
        **params,
    )

    pipe = Pipeline(steps=[
        ("preprocess", preprocess_v3),
        ("model", lgbm),
    ])

    # 1) MAE en prácticas (CV)
    scores = cross_val_score(
        pipe,
        X_tune,
        y_tune,
        scoring="neg_mean_absolute_error",
        cv=cv,
        n_jobs=-1,
    )
    mae_practice = -scores.mean()

    # 2) MAE en carrera
    pipe.fit(X_tune, y_tune)
    y_pred_race = pipe.predict(X_test_final)
    mae_race = metrics.MAE(y_test_final, y_pred_race)

    # 3) Métrica compuesta
    alpha, beta = 0.7, 0.3
    value = alpha * mae_practice + beta * mae_race

    trial.set_user_attr("mae_practice", mae_practice)
    trial.set_user_attr("mae_race", mae_race)

    return value

study_lgbm = optuna.create_study(
    direction="minimize",
    study_name="lgbm_fe_v3_practice_race_combo",
)

print("=== Optuna LightGBM (n_trials = 50) ===")
study_lgbm.optimize(objective_lgbm, n_trials=50, show_progress_bar=True)

best_lgbm_trial = study_lgbm.best_trial
print("\n=== Mejor trial LightGBM ===")
print("Valor objetivo:", best_lgbm_trial.value)
print("MAE_practice:", best_lgbm_trial.user_attrs["mae_practice"])
print("MAE_race:    ", best_lgbm_trial.user_attrs["mae_race"])
print("\nMejores hiperparámetros:")
for k, v in best_lgbm_trial.params.items():
    print(f"  {k}: {v}")

# Modelo final LGBM
best_lgbm = LGBMRegressor(
    random_state=42,
    n_jobs=-1,
    **best_lgbm_trial.params,
)

best_lgbm_pipeline = Pipeline(steps=[
    ("preprocess", preprocess_v3),
    ("model", best_lgbm),
])

best_lgbm_pipeline.fit(X_tune, y_tune)
y_pred_lgbm = best_lgbm_pipeline.predict(X_test_final)

print("\n=== Evaluación final LightGBM en carrera ===")
print(metrics.regression_report(y_test_final, y_pred_lgbm))

y_true_test_lgbm = y_test_final
y_pred_test_lgbm = y_pred_lgbm


[I 2025-12-11 03:12:37,590] A new study created in memory with name: lgbm_fe_v3_practice_race_combo


=== Optuna LightGBM (n_trials = 50) ===


  0%|          | 0/50 [00:00<?, ?it/s]

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 35, number of used features: 0
[LightGBM] [Info] Start training from score 75.227600
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the spl

### Comparación de modelos tree-based optimizados con Optuna

Probamos tres modelos de boosting (Gradient Boosting, XGBoost y LightGBM) utilizando Optuna y una métrica objetivo diseñada para balancear el ajuste en prácticas y la generalización a carrera:

J = 0.7·MAE_practice + 0.3·MAE_race

Los resultados muestran que:

- **XGBoost fue el mejor modelo para predecir tiempos de carrera**, alcanzando un MAE_race de **1.64 s**, ligeramente mejor que el Gradient Boosting tradicional optimizado (1.66 s).
- LightGBM obtuvo el peor rendimiento en este dataset (MAE ≈ 1.83 s), posiblemente debido al tamaño reducido y a la estructura de las features.
- Todos los modelos alcanzaron errores muy bajos dentro de prácticas (MAE ≈ 0.38–0.44 s), confirmando que el desafío principal no está en el modelo sino en el cambio de distribución entre prácticas y carrera (fuel load, tráfico, degradación extendida, etc.).

En resumen, **XGBoost + Optuna ofrece la mejor capacidad de generalización hacia la carrera**, aunque la diferencia con Gradient Boosting es pequeña y ambos superan ampliamente a LightGBM.
